# Case study 3: Explore country connectivity

This case investigate mobilities between a group of countries and others. The group in this study case has several large developed economies: USA, Great Britain, Japan, and Germany. The 2019 country level population flows in the four countries were first extracted using the ODT Flow API and then aggregated by origin and destination countries. Then the results were mapped using an interactive mapping library named kepler.gl (www.kepler.gl), with which users can zoom in/out the map and change display of data layers. Figure 17 shows the comparison of four countries. Widths of flow arcs are proportionate to the flow counts among countries. For clear vision, we draw two maps, and each map presents flows of a pair of countries.

## Import packages

In [23]:
import os
import math
import pandas as pd
import numpy as np
import requests
from io import StringIO
import keplergl
import geopandas as gpd
import matplotlib.pyplot as plt
import matplotlib as mpl
from keplergl import KeplerGl
import json

Prepare boundary data.

In [24]:
# country group
# G = ['USA', 'GBR', "FRA", "ITA", "JPN", "CAN", "DEU"]
G = ['USA', 'GBR', "JPN",  "DEU"]

# load country boundaries and generate centroids
country_file = r'gadm00_simplified/gadm36_00.shp'
gdf = gpd.read_file(country_file)
gdf['y'] = gdf.centroid.y
gdf['x'] = gdf.centroid.x
gdf

GID_0                                NAME_0  \
0     ABW                                 Aruba   
1     AFG                           Afghanistan   
2     AGO                                Angola   
3     AIA                              Anguilla   
4     ALA                                Ãland   
5     ALB                               Albania   
6     AND                               Andorra   
7     ARE                  United Arab Emirates   
8     ARG                             Argentina   
9     ARM                               Armenia   
10    ASM                        American Samoa   
11    ATA                            Antarctica   
12    ATF           French Southern Territories   
13    ATG                   Antigua and Barbuda   
14    AUS                             Australia   
15    AUT                               Austria   
16    AZE                            Azerbaijan   
17    BDI                               Burundi   
18    BEL                               Belgium   
19    BEN                                 Benin   
20    BES      Bonaire, Sint Eustatius and Saba   
21    BFA                          Burkina Faso   
22    BGD                            Bangladesh   
23    BGR                              Bulgaria   
24    BHR                               Bahrain   
25    BHS                               Bahamas   
26    BIH                Bosnia and Herzegovina   
27    BLM                     Saint-BarthÃ©lemy   
28    BLR                               Belarus   
29    BLZ                                Belize   
..    ...                                   ...   
226   TUR                                Turkey   
227   TUV                                Tuvalu   
228   TWN                                Taiwan   
229   TZA                              Tanzania   
230   UGA                                Uganda   
231   UKR                               Ukraine   
232   UMI  United States Minor Outlying Islands   
233   URY                               Uruguay   
234   USA                         United States   
235   UZB                            Uzbekistan   
236   VAT                          Vatican City   
237   VCT      Saint Vincent and the Grenadines   
238   VEN                             Venezuela   
239   VGB                British Virgin Islands   
240   VIR                  Virgin Islands, U.S.   
241   VNM                               Vietnam   
242   VUT                               Vanuatu   
243   WLF                     Wallis and Futuna   
244   WSM                                 Samoa   
245   XAD                 Akrotiri and Dhekelia   
246   XCA                           Caspian Sea   
247   XCL                     Clipperton Island   
248   XKO                                Kosovo   
249   XNC                       Northern Cyprus   
250   XPI                       Paracel Islands   
251   XSP                       Spratly Islands   
252   YEM                                 Yemen   
253   ZAF                          South Africa   
254   ZMB                                Zambia   
255   ZWE                              Zimbabwe   

                                              geometry          y           x  
0    POLYGON ((-69.97820 12.46986, -70.02847 12.503...  12.509652  -69.970508  
1    POLYGON ((68.52644 31.75435, 68.58202 31.75034...  33.828566   66.029628  
2    MULTIPOLYGON (((11.73347 -16.67255, 11.74014 -... -12.297561   17.548715  
3    MULTIPOLYGON (((-63.42375 18.58903, -63.42403 ...  18.221736  -63.056916  
4    MULTIPOLYGON (((21.32195 59.74986, 21.32472 59...  60.204199   20.147058  
5    MULTIPOLYGON (((19.99181 39.77597, 19.99292 39...  41.140450   20.062697  
6    POLYGON ((1.56324 42.45882, 1.55265 42.43348, ...  42.543302    1.575065  
7    MULTIPOLYGON (((52.44715 24.11619, 52.44363 24...  23.914481   54.326622  
8    MULTIPOLYGON (((-66.54916 -55.05958, -66.54639... -35.390179  -65.167107  
9    MULTIPOLYGON (((46.62959 39.22001, 4

Prepare flow data

In [25]:
dict_countries = {}
max_cnt_countries = []

min_cnt = float('inf')
max_cnt = -float('inf')

for target_place in G:
    params = {
        "operation": "get_flow_by_place",
        "source": "twitter",
        "scale": "world_country",
        "place": str(target_place),
        "begin": "01/01/2019",
        "end": "12/31/2019",
        "direction": "both"
    }

    q = r'http://gis.cas.sc.edu/GeoAnalytics/REST'
    r = requests.get(q, params=params)
    df = pd.read_csv(StringIO(r.text), header=None, names=['d_place', 'cnt'])
    df = df[df['d_place'] != target_place] # remove intra-flows
    df = df.sort_values("cnt", ascending=False)

    
    min_cnt = min(min_cnt, df['cnt'].min())
    max_cnt = max(max_cnt, df['cnt'].max())
    max_cnt_countries.append(df['cnt'].max())
    dict_countries[target_place] = {}
    dict_countries[target_place]['dataframe'] = df
    dict_countries[target_place]['max_cnt'] = df['cnt'].max()


Set the start and end points of flows

In [26]:
def set_endpoints(G, dict_countries):
    for target_place in G:        
        df_c = dict_countries[target_place]['dataframe']
        df_c["o_place"] = target_place
        df_c = df_c.set_index("o_place").join(gdf.set_index("GID_0"), how="left")
        df_c = df_c.drop(['NAME_0', "geometry"], axis=1)
        df_c = df_c.rename(columns={"y": "o_lat", 'x': "o_lon"})
        df_c['o_place'] = df_c.index
        df_c = df_c.set_index("d_place").join(gdf.set_index("GID_0"), how="left")
        df_c = df_c.drop(['NAME_0', "geometry"], axis=1)
        df_c = df_c.rename(columns={"y": "d_lat", 'x': "d_lon"})
        df_c['d_place'] = df_c.index
        
        # remove flows in the group
#         df_c = df_c[df_c['d_place'] != df_c['o_place']]
#         df_c = df_c[~df_c['d_place'].isin(G)]

        dict_countries[target_place]['dataframe'] = df_c
    
set_endpoints(G, dict_countries)

## Show the map

The map shows the inter-unit flows of the selected countries in the group. Widths of arcs indicate the number of flows; the more the wider.

In [27]:
# load the config file for keplergl
kepler_cfg_file = r'kepler_cfg_G.json'
kepler_cfg = json.load(open(kepler_cfg_file, 'r'))


map_gl = KeplerGl(height = 600)
# map_2.config = kepler_cfg

# add data lyaer to map
max_arc_width = 20

for idx in range(len(G)):

    
    dataId = kepler_cfg['config']['visState']['layers'][idx]['config']['dataId']

    map_gl.add_data(data=dict_countries[dataId]['dataframe'], name=dataId)  
    
    # calculate the arc width. 
    arc_width = dict_countries[dataId]['max_cnt']/max(max_cnt_countries) * max_arc_width
    arc_width = int(arc_width)
    kepler_cfg['config']['visState']['layers'][idx]['config']['visConfig']['sizeRange'] = [0, arc_width]
    


# show the map
map_gl.config = kepler_cfg
map_gl

User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


A Jupyter Widget

If needed, save the config

In [28]:
cfg = map_gl.config
with open('kepler_cfg_G.json', 'w') as fp:
    json.dump(cfg, fp,  indent=2)